In [2]:
import csv
import pandas as pd 
from pymongo import MongoClient

import requests
from bs4 import BeautifulSoup


ModuleNotFoundError: No module named 'bs4'

In [2]:
# Connect to MongoDB
client = MongoClient("mongodb://localhost:27017/")
db = client["myDatabase"]
source_collection = db["data"]

In [9]:
# Export translated data to a CSV file #bu dosyayı json olarak indirdim
"""yeni_data = list(source_collection.find())
print(yeni_data)"""

In [3]:
#csv dosyası olarak yüklenmesi
df=pd.read_json('myDatabase.data.json')
print(df.head())

                                    _id                             title  \
0  {'$oid': '66a1020f29abc84d21689044'}               Mental Note Vol. 24   
1  {'$oid': '66a1020f29abc84d21689045'}         Your Brain On Coronavirus   
2  {'$oid': '66a1020f29abc84d21689046'}                    Mind Your Nose   
3  {'$oid': '66a1020f29abc84d21689047'}          The 4 Purposes of Dreams   
4  {'$oid': '66a1020f29abc84d21689048'}  Surviving a Rod Through the Head   

                                                 url                 authors  \
0  https://medium.com/invisible-illness/mental-no...            ['Ryan Fan']   
1  https://medium.com/age-of-awareness/how-the-pa...       ['Simon Spichak']   
2  https://medium.com/neodotlife/mind-your-nose-f...                      []   
3  https://medium.com/science-for-real/the-4-purp...  ['Eshan Samaranayake']   
4  https://medium.com/live-your-life-on-purpose/s...        ['Rishav Sinha']   

                          timestamp  \
0  2020-12-26 03:

In [4]:
df.head()

_id                             title  \
0  {'$oid': '66a1020f29abc84d21689044'}               Mental Note Vol. 24   
1  {'$oid': '66a1020f29abc84d21689045'}         Your Brain On Coronavirus   
2  {'$oid': '66a1020f29abc84d21689046'}                    Mind Your Nose   
3  {'$oid': '66a1020f29abc84d21689047'}          The 4 Purposes of Dreams   
4  {'$oid': '66a1020f29abc84d21689048'}  Surviving a Rod Through the Head   

                                                 url                 authors  \
0  https://medium.com/invisible-illness/mental-no...            ['Ryan Fan']   
1  https://medium.com/age-of-awareness/how-the-pa...       ['Simon Spichak']   
2  https://medium.com/neodotlife/mind-your-nose-f...                      []   
3  https://medium.com/science-for-real/the-4-purp...  ['Eshan Samaranayake']   
4  https://medium.com/live-your-life-on-purpose/s...        ['Rishav Sinha']   

                          timestamp  \
0  2020-12-26 03:38:10.479000+00:00   
1  2020-09-23 22:10:17.126000+00:00   
2  2020-10-10 20:17:37.132000+00:00   
3  2020-12-21 16:05:19.524000+00:00   
4  2020-02-26 00:01:01.576000+00:00   

                                                tags  
0  ['Mental Health', 'Health', 'Psychology', 'Sci...  
1  ['Mental Health', 'Coronavirus', 'Science', 'P...  
2  ['Biotechnology', 'Neuroscience', 'Brain', 'We...  
3  ['Health', 'Neuroscience', 'Mental Health', 'P...  
4  ['Brain', 'Health', 'Development', 'Psychology...

In [5]:
df.dtypes

_id          object
title        object
url          object
authors      object
timestamp    object
tags         object
dtype: object

In [8]:
for i in df.columns:
    print(df[i].apply(lambda x:type(x)).head(1))

0    <class 'dict'>
Name: _id, dtype: object
0    <class 'str'>
Name: title, dtype: object
0    <class 'str'>
Name: url, dtype: object
0    <class 'str'>
Name: authors, dtype: object
0    <class 'str'>
Name: timestamp, dtype: object
0    <class 'str'>
Name: tags, dtype: object


In [9]:
#içeriklerin saklanacağı bir liste oluştrun
contents=[]
#her url için içeriği çekin 

for url in df['url']:
    try:
        response=requests.get(url)
        soup=BeautifulSoup(response.content,'html.parser')

        #medium içeriğini çekmek için uygun seçiciyi kullanın
        article_content=soup.find('articles')
        content=article_content.get_text(separator='') if article_content else 'content not found'

        contents.append(content)
    except Exception as e:
        contents.append(f'error retrieving content: {e}')

#içerikleri veri çerçevesine ekleyin.
df['content']= contents

#yeni veri kümesini kontrol edin
print(df.head())

In [ ]:

#modeleğitimi için test valid değerleriğ oluşturma 

from sklearn.model_selection import train_test_split

X_train, X_val, y_train, y_val = train_test_split(translated_data, translated_data, test_size=0.2, random_state=42)

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.svm import SVC

vectorizer = TfidfVectorizer()
X_train_transformed = vectorizer.fit_transform(X_train)
X_val_transformed = vectorizer.transform(X_val)

model = SVC()
model.fit(X_train_transformed, y_train)

In [ ]:
from sklearn.metrics import accuracy_score

y_pred = model.predict(X_val_transformed)
accuracy = accuracy_score(y_val, y_pred)
print(f"Accuracy: {accuracy:.2f}")